In [1]:
# 引用需要的library
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.neighbors import KNeighborsClassifier
from sklearn.tree import DecisionTreeClassifier
from sklearn.svm import SVC
from sklearn.ensemble import RandomForestClassifier
from sklearn.ensemble import AdaBoostClassifier
from sklearn.ensemble import GradientBoostingClassifier
from xgboost import XGBClassifier
from lightgbm import LGBMClassifier
from matplotlib import pyplot as plt
import helper
import joblib
import os
import jieba
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.tree import plot_tree

c:\ProgramData\Anaconda3\lib\site-packages\dask\dataframe\utils.py:369: FutureWarning: pandas.Int64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  _numeric_index_types = (pd.Int64Index, pd.Float64Index, pd.UInt64Index)
c:\ProgramData\Anaconda3\lib\site-packages\dask\dataframe\utils.py:369: FutureWarning: pandas.Float64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  _numeric_index_types = (pd.Int64Index, pd.Float64Index, pd.UInt64Index)
c:\ProgramData\Anaconda3\lib\site-packages\dask\dataframe\utils.py:369: FutureWarning: pandas.UInt64Index is deprecated and will be removed from pandas in a future version. Use pandas.Index with the appropriate dtype instead.
  _numeric_index_types = (pd.Int64Index, pd.Float64Index, pd.UInt64Index)


In [2]:
# 从文件中读取停用词列表
def load_stopwords(stopwords_file):
    with open(stopwords_file, 'r', encoding='utf-8') as f:
        stopwords = [line.strip() for line in f]
    return stopwords

stopwords_file = './stop_words.txt'  #stop_words.txt文件路径

#加载停用词文件
stop_words = load_stopwords(stopwords_file)

In [3]:
# 从文本文件中读数据
# 读取到的内容
# X=评论（string）， y=情感分类（0/1）
import re
folder_path = './user_comments'  # 请将此处替换为您的文件夹路径
X = []
y = []

for root, dirs, files in os.walk(folder_path):
    for dir in dirs:
        if dir == 'neg':
            label = 0
        elif dir == 'pos':
            label = 1
        else:
            continue
        for file in os.listdir(os.path.join(folder_path, dir)):
            if file.endswith('.txt'):
                file_path = os.path.join(folder_path, dir, file)
                with open(file_path, 'r', encoding='gb2312',errors='ignore') as f:
                    content = f.read()
                    content = content.strip().replace(" ", "")
                    #if content == "": break
                print(content)
                # 使用jieba进行分词并过滤掉停用词
                words = ' '.join([word for word in jieba.cut(content) if word not in stop_words])
                #去除空字符串
                #words = [word for word in words if word.strip()]
                #使用空格连接分词结果
                #words = ' '.join(words)
                #使用正则表达式去除多余的空白字符
                words = re.sub(r'\s+', ' ', words)
                X.append(words)
                y.append(label)


Building prefix dict from the default dictionary ...
Loading model from cache C:\Users\imuyo\AppData\Local\Temp\jieba.cache


标准间太差房间还不如3星的而且设施非常陈旧.建议酒店把老的标准间从新改善.


Loading model cost 0.643 seconds.
Prefix dict has been built successfully.


服务态度极其差，前台接待好象没有受过培训，连基本的礼貌都不懂，竟然同时接待几个客人；

大堂副理更差，跟客人辩解个没完，要总经理的电话投诉竟然都不敢给。要是没有作什么亏心事情，跟本不用这么怕。
地理位置还不错，到哪里都比较方便，

但是服务不象是豪生集团管理的，比较差。

下午睡了一觉并洗了一个澡，本来想让酒店再来打扫一下，所以，打开了，请打扫的服务灯，可是到晚上回酒店，发现打扫得服务灯被关掉了，而房间还是没有打扫过。
1。我住的是靠马路的标准间。房间内设施简陋，并且的房间玻璃窗户外还有一层幕墙玻璃，而且不能打开，导致房间不能自然通风，采光不好。

2。吃了三顿早餐，品种少得可怜。

3。二楼餐厅被租出去了，价格特贵。原来订餐时告之房客可以打九折（房间服务指南里也明明白白写的，等到结帐时却告之海鲜和酒水是不能打折的，而且没有发票，找来经理才好不容易在第二天拿到发票。综合来说与四星级差距太大了！
我这次是第5次住在长春的雁鸣湖大酒店。昨晚夜里停电。深夜我睡着了。我的钱包被内贼进入我的房间，偷了我近1000元和4张信用卡。。。

我的证件和外币，数码相机等都在房间的保险箱里，原封不动。我打了好几个小时的长途电话来处理我的信用卡的冻结。我报案了，这个4星酒店的保安摄像探头竟然坏了，没有修理！

保安还查房卡入门时间，就是没有其他人在深夜进入我的房间。难道内贼不会用其他高明的方式进入吗？我的羽绒服也被这个内贼放在地上！我醒来时没有多想！近中午时我才发觉钱包少了现金和信用卡！

还有，这家酒店的态度很差！没有同情心！我之前授权的2000元，我打了国际电话，银行说两天前我入酒店的2000元授权了，可是酒店的财务不领情，说中国银行没有授权。我又打了国际电话，我的银行说通过了！

这家4星级的酒店不负责，认为不可能发生，我报案了，我下次再也不住这个1星不到的服务态度，很可耻！

我还要把这个事件说给那些想定这个酒店的住客。酒店为何停电，摄像头坏得也太凑巧了来让大家知道这种内贼行为是要强力打击的。

好了，不说了！！！千元丢了小事。酒店的处理态度我很反感！我强力告诉大家和提醒其他人不要到该酒店！
前台checkin花了20分钟，checkout25分钟，这是服务态度和没有做到位。

信用卡刷了好几次，不愿意用手工打电话授权。典型国营企业的极差的服务态度。
]有或者很少o房g!梯炔坎辉

In [4]:
import pandas as pd
from sklearn.utils import shuffle
data = pd.DataFrame({'sentiment': y,'comment': X})
data = shuffle(data)
print(data.head(50))

      sentiment                                            comment
5698          1                               房间 服务 停车场 驾车者 旅行者 的士
2394          0  图 交通 选择 市长 大厦 市长 大厦 新 酒店 可一 进门 感觉 失望 ― ― 大堂 超级...
3808          1                     酒店 位置 不错 设施 齐全 价格 高 停车 不太 收费 高
5463          1  入住 房间 开窗 空气流通 欠 满意 遗憾 宾馆 反馈 2008 年 月 10 日 饭店 房...
948           0  从没 见过 残旧 五星级 酒店 电梯 走廊 房间内 铺设 地毯 惨不忍睹 形容 电梯 地毯 ...
2037          0  酒店 住 环境 差 卫生 打扫 前台 服务态度 差 保健 中心 服务员 素质 差 足浴 不到...
1366          0  帮 客户 订 担心 地段 最终 比较满意 特别 不好 地方 下次 追求 特价 房 换莫泰 好...
1445          0                       适合 做个 落脚点 环境 嘈杂 房间 陈旧 窗户 关不上
4914          1  房间 装修 床垫 住 舒服 卫生 干净 服务 结帐 速度 挺快 酒店 位置 交通 餐厅 海鲜...
1909          0  招待所 装修 倒 干净 服务 设施 院子 晚上 12 点 要关 大门 晚上 回来 晚 敲门 ...
842           0  服务 差 环境 不好 建议 别去 提前 星期 就定 加床 前台 告诉 能加 闯 房间 加床 ...
3704          1    服务 仔细 房间 陈色 虽旧 用品 挺 干净 服务员 素质 拾 钱包 想 办法 还给 非常感激
4178          1  评论 才定 这家 酒店 没想到 换来 惊喜 房间 窗户 花园 没想到 能住 苏州 园林 安静...
2784          0                    酒店 地理位置 不错 交通 便利 酒店 外观 房间 设

In [5]:
X=np.array(X)
y=np.array(y)
X.shape


(6000,)

In [6]:
# print(X.shape)
# (4905,)

# 初始化文本向量化
vectorizer = CountVectorizer()
# 使用CountVectorizer进行文本向量化
X = vectorizer.fit_transform(X)
#将稀疏矩阵转为密集矩阵dense_matrix
#dense_matrix = X.toarray()
print(f"查看文本向量化后结果：{X.toarray()}")
print("------")
print(f"查看文本向量化后矩阵形状：{X.shape}")
print("------")
#遍历稀疏矩阵的行或列来逐行或逐列查看数据
for row in range(X.shape[0]):
    print(f"查看向量化矩阵第{row}行：{X.getrow(row)}")
    print("------")
# 非零元素的位置
print(f"查看非零元素的位置：{X.nonzero()}")
print("------")
# 非零元素的值
print(f"查看非零元素的值：{X.data}")
# 打印转化为词向量的X数据，是一个稀疏的矩阵(4905, 18300)
#print(X.toarray())
#print(X.shape)
#（4249，15399）



查看文本向量化后结果：[[0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 ...
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]
 [0 0 0 ... 0 0 0]]
------
查看文本向量化后矩阵形状：(6000, 20490)
------
查看向量化矩阵第0行：  (0, 12485)	2
  (0, 10033)	1
  (0, 17639)	1
  (0, 19622)	1
  (0, 9006)	1
  (0, 19114)	1
  (0, 11061)	1
------
查看向量化矩阵第1行：  (0, 12148)	1
  (0, 4650)	1
  (0, 10734)	2
  (0, 5510)	1
  (0, 6779)	1
  (0, 15449)	1
  (0, 4268)	1
  (0, 7922)	2
  (0, 7117)	1
  (0, 4699)	1
  (0, 18436)	1
  (0, 13258)	1
  (0, 9602)	1
  (0, 14799)	1
  (0, 10311)	1
  (0, 2599)	1
  (0, 18212)	1
  (0, 1797)	1
------
查看向量化矩阵第2行：  (0, 10033)	1
  (0, 19114)	2
  (0, 6658)	1
  (0, 1892)	1
  (0, 12138)	3
  (0, 17907)	1
  (0, 17921)	1
  (0, 19759)	1
  (0, 15896)	1
  (0, 1516)	1
  (0, 1210)	1
  (0, 12257)	1
  (0, 10161)	4
  (0, 10155)	1
  (0, 11807)	1
  (0, 5441)	1
  (0, 3969)	1
------
查看向量化矩阵第3行：  (0, 12485)	1
  (0, 10033)	3
  (0, 17639)	1
  (0, 10155)	1
  (0, 20223)	1
  (0, 10034)	1
  (0, 15861)	1
  (0, 14575)	1
  (0, 9968)	1
  (0, 1026)	1
  

In [7]:
voca = vectorizer.vocabulary_
print(voca)
# vocabulary dict

# 对dict重新排序，按照value的顺序打印dict
voca=sorted(voca.items(), key=lambda x: x[1])
for item in voca:
    print(item)

{'标准间': 12485, '房间': 10033, '设施': 17639, '陈旧': 19622, '建议': 9006, '酒店': 19114, '改善': 11061, '服务态度': 12148, '前台': 4650, '接待': 10734, '受过': 5510, '培训': 6779, '礼貌': 15449, '几个': 4268, '客人': 7922, '大堂': 7117, '副理': 4699, '辩解': 18436, '没完': 13258, '总经理': 9602, '电话': 14799, '投诉': 10311, '亏心事': 2599, '跟本': 18212, '不用': 1797, '地理位置': 6658, '不错': 1892, '服务': 12138, '象是': 17907, '豪生': 17921, '集团': 19759, '管理': 15896, '下午': 1516, '一觉': 1210, '本来': 12257, '打扫': 10161, '打开': 10155, '晚上': 11807, '发现': 5441, '关掉': 3969, '马路': 20223, '房间内': 10034, '简陋': 15861, '玻璃窗': 14575, '户外': 9968, '一层': 1026, '幕墙': 8706, '玻璃': 14571, '导致': 8107, '自然通风': 16772, '采光': 19152, '不好': 1695, '三顿': 1401, '早餐': 11598, '品种': 6179, '少得': 8295, '可怜': 5687, '二楼': 2577, '餐厅': 20128, '租出去': 15537, '价格': 3007, '特贵': 14427, '订餐': 17582, '时告': 11629, '房客': 10002, '九折': 2437, '服务指南': 12149, '明明白白': 11699, '结帐': 16183, '海鲜': 13675, '酒水': 19128, '打折': 10166, '发票': 5450, '经理': 16159, '好不容易': 7563, '第二天': 15794, '拿到': 10516, '综合': 1624

In [8]:
# 调用jieba分词
# 文本向量化：1. 类one-hot编码 2. count思想 3. tf-idf思想
# 返回 X=评论向量（list），y=情感分类（0/1）

In [9]:
# 切分数据集为X_train, y_train, X_test, y_test
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

In [10]:
type(X_train)
type(X_test)

scipy.sparse.csr.csr_matrix

In [11]:
# 数据预处理：标准化/归一化

_mean = X_train.mean()
_std = X_train.std() + 1e-9
X_train = (X_train - _mean) / _std
X_test = (X_test - _mean) / _std
# 稀疏矩阵降维：PCA, 低优先级

AttributeError: std not found

In [ ]:
# 调用各分类模型，训练
# KNeighborsClassifier
# DecisionTreeClassifier
# 构建一个模型
model = DecisionTreeClassifier(max_depth=2)

# 训练模型
model.fit(X=X_train, y=y_train)
# 绘制训练好的决策树
plot_tree(model)

# SVC
# RandomForestClassifier
# AdaBoostClassifier
# GradientBoostingClassifier
# XGBClassifier
# LGBMClassifier

In [ ]:
# 调用训练完毕的模型，做预测
y_pred = model.predict(X_test)

In [ ]:
# 计算各模型的acc，训练时间，预测时间
acc = (y_pred == y_test).mean()
print(acc)

In [ ]:
# 保存模型到models文件夹
joblib.dump(value=model, filename="./models/decisiontree.model")

In [ ]:
predict_model = joblib.load("./models/decisiontree.model")
y_result = predict_model.predict(X_test[20])
print(y_result)

In [ ]:
# Precision-Recall Curve
# 柱状图，能够一眼看出各数据的大小，比较数据之间的差别